In [169]:
import pickle
import pandas as pd
import numpy as np
import time
from sklearn.preprocessing import label_binarize
from sklearn.metrics import roc_auc_score
from sklearn.utils import shuffle
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import KFold, StratifiedKFold, RepeatedKFold
import torch
import torch.nn as nn
from tqdm.auto import tqdm

pd.set_option('display.max_columns', 500)

#### Functions and classes

In [27]:
def transfer_weights(source_model, dest_model):
    dest_model.rnn_ts.weight_hh_l0.data = source_model.rnn_ts.weight_hh_l0.data
    dest_model.rnn_ts.weight_ih_l0.data = source_model.rnn_ts.weight_ih_l0.data
    dest_model.rnn_ts.bias_hh_l0.data = source_model.rnn_ts.bias_hh_l0.data
    dest_model.rnn_ts.bias_ih_l0.data = source_model.rnn_ts.bias_ih_l0.data
    return dest_model

def confidence_interval(a):
    low = np.percentile(a, 2.5)
    high = np.percentile(a, 97.5)
    return '95%% CI: %.3f-%.3f' % (low, high) 

In [20]:
def class_weights(y_flat, n_classes=2):
    n = len(y_flat)
    weights = []
    for i in range(n_classes):
        n_in_class = len(np.where(y_flat==i)[0])
        weights.append(n/(n_classes*n_in_class))
    return torch.FloatTensor(weights)

class Dataset:
    def __init__(self, X_ts, y, X_extra=None):
        self.X_ts = [torch.FloatTensor(x).cuda() for x in X_ts]
        self.y = torch.LongTensor(y).cuda()
        self.seq_lens = torch.LongTensor([len(x) for x in X_ts]).cuda()
        
        if X_extra is not None:
            self.X_extra = [torch.FloatTensor(x).cuda() for x in X_extra]
        else:
            self.X_extra = None
            
        self.pad_value = -999
        self.input_dim_ts = X_ts[0].shape[1]
        self.input_dim_extra= X_extra[0].shape[1] if X_extra is not None else None
        self.class_weights = class_weights(y).cuda()
        
    def __len__(self):
        return len(self.y)
    
    def __getitem__(self, i):
        return {
            'x_ts': self.X_ts[i],
            'x_extra': self.X_extra[i] if self.X_extra is not None else None,
            'y': self.y[i],
            'seq_lens': self.seq_lens[i],
        }
    
    def collate_fn(self, samples):
        return {
            'y': torch.stack([sample['y'] for sample in samples]),
            'x_ts': nn.utils.rnn.pad_sequence([sample['x_ts'] for sample in samples], batch_first=True, padding_value=self.pad_value),
            'x_extra': nn.utils.rnn.pad_sequence([sample['x_extra'] for sample in samples], batch_first=True, padding_value=self.pad_value) if self.X_extra is not None else None,
            'seq_lens': torch.stack([sample['seq_lens'] for sample in samples]),
        }
    
    def loader(self, n=None, **kwargs):
        if n is not None:
            return torch.utils.data.DataLoader(dataset=torch.utils.data.Subset(self, indices=range(n)),
                                               collate_fn=self.collate_fn,
                                               **kwargs)
        else:
            return torch.utils.data.DataLoader(dataset=self, collate_fn=self.collate_fn, **kwargs)

def load_idealist_dataset():
    with open('/home/shickelb/IntelligentICU/datasets/idealist.pkl', 'rb') as f:
        idealist_data = pickle.load(f)
        
    train_data = Dataset(X_ts=idealist_data['X_train'], y=np.array([y[-1] for y in idealist_data['y_train']]), X_extra=None)
    val_data = Dataset(X_ts=idealist_data['X_val'], y=np.array([y[-1] for y in idealist_data['y_val']]), X_extra=None)
    test_data = Dataset(X_ts=idealist_data['X_test'], y=np.array([y[-1] for y in idealist_data['y_test']]), X_extra=None)
    
    return train_data, val_data, test_data, idealist_data['median'], idealist_data['scaler']

In [100]:
def get_mask(x, x_lens):
    mask = torch.arange(x.size(1), device=x.device)
    mask = (mask[None, :] < x_lens[:, None]).float()
    return mask

def get_predictions(model, loader):
    test_y_true = []
    test_y_pred = []
    
    model.eval()
    with torch.no_grad():
        for i, batch in enumerate(loader):
            outputs = model(batch)
            
            y_true = batch['y'].view(-1).cpu().numpy()
            y_pred = outputs['y'].cpu().detach().numpy()
            
            test_y_true += list(y_true)
            test_y_pred += list(y_pred)
            
    test_y_true = np.array(test_y_true)
    test_y_pred = np.array(test_y_pred)
    
    test_y_pred = test_y_pred[:, 1]
    
    return test_y_true, test_y_pred

def get_auc(model, test_loader):
    y_true, y_pred = get_predictions(model, test_loader)
    return roc_auc_score(y_true, y_pred)

def train(model, optimizer, criterion, train_loader, val_loader, patience=4, epochs=9999, filepath='tmp.pth', verbose=True):
    best_val_auc = -float('inf')
    patience_counter = patience

    for epoch in range(epochs):
        t0 = time.time()
        model.train()
        train_losses = []
        pbar = tqdm(train_loader, leave=False)
        for i, batch in enumerate(pbar):
            model.zero_grad()
            outputs = model(batch)
            loss = criterion(outputs, batch)
            train_losses.append(loss.item())
            loss.backward()
            optimizer.step()

            if i % 100 == 0:
                pbar.set_postfix({'loss': np.mean(train_losses)})

        # Validation: epoch metrics
        val_losses, val_y_true, val_y_pred = [], [], []
        model.eval()
        with torch.no_grad():
            for j, val_batch_inputs in enumerate(val_loader):
                val_batch_outputs = model(val_batch_inputs)
                val_losses.append(criterion(val_batch_outputs, val_batch_inputs).item())

                y_true = val_batch_inputs['y'].cpu().numpy()
                y_pred = val_batch_outputs['y'].cpu().detach().numpy()

                val_y_true += list(y_true)
                val_y_pred += list(y_pred)        

        val_y_true = np.array(val_y_true)
        val_y_pred = np.array(val_y_pred)
        
        val_auc = roc_auc_score(val_y_true[:], val_y_pred[:, 1])
        
        s = '[E%-3s@%4ss]  ' % (epoch, int(time.time() - t0))
        s += 'loss: %.3f  ' % np.mean(train_losses)
        s += 'val_loss: %.3f  ' % np.mean(val_losses)
        s += 'val_auc: %.3f' % val_auc
        
        if verbose:
            print(s)

        if val_auc > best_val_auc:
            best_val_auc = val_auc
            patience_counter = patience
            torch.save(model.state_dict(), filepath)
        else:
            patience_counter -= 1
            if patience_counter == 0:
                break
    model.load_state_dict(torch.load(filepath))
    model.eval()
    return model, best_val_auc

class PackedGRU(nn.Module):
    def __init__(self, input_size, hidden_size, n_layers=1, bias=True, dropout=0, bidirectional=False, pad_value=-999):
        super(PackedGRU, self).__init__()
        self.pad_value = pad_value
        self.gru = nn.GRU(input_size=input_size,
                          hidden_size=hidden_size,
                          num_layers=n_layers,
                          bias=bias,
                          batch_first=True,
                          dropout=dropout,
                          bidirectional=bidirectional)

    def forward(self, x, h0=None):
        batch_size = x.size(0)
        mask = (x != self.pad_value).float()
        lens = mask.sum(dim=1)[:, 0]
        sorted_lens, sorted_idx = torch.sort(lens, 0, descending=True)
        _, unsorted_idx = torch.sort(sorted_idx, 0, descending=False)
        x = x[sorted_idx]
        x = nn.utils.rnn.pack_padded_sequence(x, sorted_lens.long(), batch_first=True)
        output, h_n = self.gru(x, h0)
        output, _ = nn.utils.rnn.pad_packed_sequence(output, batch_first=True, padding_value=self.pad_value)
        output = output[unsorted_idx]
        h_n = h_n[:, unsorted_idx, :]
        h_n = h_n.transpose(0, 1).contiguous().view(batch_size, -1)
        return output, h_n

    def flatten_parameters(self):
        self.gru.flatten_parameters()

class Model(nn.Module):
    def __init__(self, train_data, hidden_dim=64, dropout=0, activation=nn.ReLU):
        super().__init__()
        
        self.rnn_ts = PackedGRU(train_data.input_dim_ts, hidden_dim)
        
        if train_data.X_extra is not None:
            self.rnn_extra = PackedGRU(train_data.input_dim_extra, hidden_dim)
            self.linear = nn.Linear(hidden_dim * 2, 2)
        else:
            self.rnn_extra = None
            self.linear = nn.Linear(hidden_dim, 2)
            
    def forward(self, batch):
        x_ts = batch['x_ts']
        x_extra = batch['x_extra']
        seq_lens = batch['seq_lens']
        mask = get_mask(x_ts, seq_lens)
        
        _, h_ts = self.rnn_ts(x_ts) # h: (batch, timesteps, hidden)
        
        if self.rnn_extra is not None:
            _, h_extra = self.rnn_extra(x_extra) # h: (batch, timesteps, hidden)
            h = torch.cat([h_ts, h_extra], dim=-1)
        else:
            h = h_ts
        
        y_pred = self.linear(h) # (batch, timesteps, n_labels)
        #y_pred[mask.unsqueeze(-1).expand_as(y_pred) == 0] = -999
    
        return {'y': y_pred}
    
class Loss:
    def __init__(self, train_data, weighted=True):
        if weighted:
            self.criterion = nn.CrossEntropyLoss(weight=train_data.class_weights)
        else:
            self.criterion = nn.CrossEntropyLoss()
        
    def __call__(self, outputs, inputs):
        y_true = inputs['y']
        y_pred = outputs['y']
        
        #print('y_true:', y_true.shape)
        #print('y_pred:', y_pred.shape)
        
        #batch_size, timesteps, n_labels = y_pred.shape
        
        #y_true = y_true.view(-1)
        #y_pred = y_pred.view(-1, 2)
        
        loss = self.criterion(y_pred, y_true)
        return loss

#### IDEALIST

In [22]:
idealist_train_data, idealist_val_data, idealist_test_data, idealist_median, idealist_scaler = load_idealist_dataset()

In [25]:
idealist_model = Model(idealist_train_data).cuda()

idealist_model, idealist_model_best_val_auc = train(model=idealist_model,
                                          optimizer=torch.optim.Adam(idealist_model.parameters(), weight_decay=1e-2),
                                          criterion=Loss(idealist_train_data),
                                          train_loader=idealist_train_data.loader(batch_size=32, shuffle=True),
                                          val_loader=idealist_val_data.loader(batch_size=128, shuffle=False),
                                          patience=3)

[E0  @   7s]  loss: 0.579  val_loss: 0.569  val_auc: 0.756


[E1  @   7s]  loss: 0.568  val_loss: 0.570  val_auc: 0.761


[E2  @   7s]  loss: 0.565  val_loss: 0.565  val_auc: 0.763


[E3  @   7s]  loss: 0.560  val_loss: 0.566  val_auc: 0.768


[E4  @   7s]  loss: 0.559  val_loss: 0.563  val_auc: 0.768


...

[E14 @   7s]  loss: 0.551  val_loss: 0.559  val_auc: 0.775


[E15 @   7s]  loss: 0.550  val_loss: 0.558  val_auc: 0.777


[E16 @   7s]  loss: 0.550  val_loss: 0.555  val_auc: 0.773


[E17 @   7s]  loss: 0.549  val_loss: 0.561  val_auc: 0.769


[E18 @   7s]  loss: 0.548  val_loss: 0.558  val_auc: 0.772


In [28]:
get_auc(idealist_model, idealist_test_data.loader(batch_size=128, shuffle=False))

0.7766781411359724

## Intelligent ICU

#### Load data

In [182]:
iicu_data = pd.read_csv('/home/shickelb/IntelligentICU/datasets/iicu.csv', index_col='icustay_id')

EXTRA_COLS = ['mean', 'max', 'min', 'variance', 'sd', 'IQR', 'RMSSD', 'RMSSD_SD', 'number_immobile']
              
TS_COLS = [c for c in iicu_data.columns if c not in EXTRA_COLS+['y'] and 'AU'not in c]

iicu_label_map = dict([x for x in iicu_data.reset_index()[['icustay_id', 'y']].values])
iicu_ids = np.array(sorted(iicu_label_map.keys()))
iicu_labels = np.array([iicu_label_map[id_] for id_ in iicu_ids])

iicu_data[:2]

bilirubin_min  bilirubin_max  bilirubin_mean  bilirubin_median  \
icustay_id                                                                   
0                     1.5            1.5             1.5               1.5   
0                     NaN            NaN             NaN               NaN   

            bilirubin_var  bilirubin_std  bilirubin_sum  bilirubin_count  \
icustay_id                                                                 
0                     NaN            NaN            1.5              1.0   
0                     NaN            NaN            0.0              0.0   

            gcs_min  gcs_max  gcs_mean  gcs_median   gcs_var   gcs_std  \
icustay_id                                                               
0              10.0     11.0     10.25        10.0  0.250000  0.500000   
0               3.0     11.0      9.00        10.0  6.285714  2.507133   

            gcs_sum  gcs_count  bp_diastolic_min  bp_diastolic_max  \
icustay_id                                                           
0              41.0        4.0              47.0              82.0   
0              72.0        8.0              33.0             105.0   

            bp_diastolic_mean  bp_diastolic_median  bp_diastolic_var  \
icustay_id                                                             
0                   59.666667                 59.5         82.666667   
0                   60.184080                 56.0        169.050945   

            bp_diastolic_std  bp_diastolic_sum  bp_diastolic_count  \
icustay_id                                                           
0                   9.092121            1432.0                24.0   
0                  13.001959           12097.0               201.0   

            bp_systolic_min  bp_systolic_max  bp_systolic_mean  \
icustay_id                                                       
0                     119.0            197.0        142.291667   
0                     100.0            221.0        138.457711   

            bp_systolic_median  bp_systolic_var  bp_systolic_std  \
icustay_id                                                         
0                        139.0       350.389493        18.718694   
0                        132.0       666.849453        25.823428   

            bp_systolic_sum  bp_systolic_count  creatinine_min  \
icustay_id                                                       
0                    3415.0               24.0            0.40   
0                   27830.0              201.0            0.35   

            creatinine_max  creatinine_mean  creatinine_median  \
icustay_id                                                       
0                     0.47             0.43               0.42   
0                     0.47             0.41               0.41   

            creatinine_var  creatinine_std  creatinine_sum  creatinine_count  \
icustay_id                                                                     
0                   0.0007        0.026458            2.15               5.0   
0                   0.0072        0.084853            0.82               2.0   

            platelets_min  platelets_max  platelets_mean  platelets_median  \
icustay_id                                                                   
0                   220.0          278.0          243.75             238.5   
0                   221.0          244.0          232.50             232.5   

            platelets_var  platelets_std  platelets_sum  platelets_count  \
icustay_id                                                                 
0              657.583333      25.643388          975.0              4.0   
0              264.500000      16.263456          465.0              2.0   

            pao2_min  pao2_max  pao2_mean  pao2_median  pao2_var   pao2_std  \
icustay_id                                                                    
0              188.0     258.0      223.0        223.0    2450.0  49.497475   
0 

In [183]:
y_iicu = pd.DataFrame(iicu_label_map.items()).rename(columns={0: 'icustay_id', 1: 'y'}).set_index('icustay_id')
y_iicu[:5]

y
icustay_id   
0           0
1           0
2           0
3           0
4           0

# II. Transfer Learning

#### Trying single split

In [184]:
def load_iicu_fold(ids_train, ids_val, ids_test, extra, transfer):
    df = iicu_data.copy()
    
    # Extra columns
    df.loc[:, EXTRA_COLS] = df.loc[:, EXTRA_COLS].fillna(0)
    scaler = StandardScaler()
    df.loc[ids_train, EXTRA_COLS] = scaler.fit_transform(df.loc[ids_train, EXTRA_COLS])
    df.loc[ids_val, EXTRA_COLS] = scaler.transform(df.loc[ids_val, EXTRA_COLS])
    df.loc[ids_test, EXTRA_COLS] = scaler.transform(df.loc[ids_test, EXTRA_COLS])
    
    # EHR columns
    df = df.groupby(df.index).ffill()
    
    if transfer:
        df.loc[:, TS_COLS] = df.loc[:, TS_COLS].fillna(idealist_median)
    else:
        df.loc[:, TS_COLS] = df.loc[:, TS_COLS].fillna(df.loc[ids_train, TS_COLS].median())
    
    if transfer:
        df.loc[:, TS_COLS] = idealist_scaler.transform(df.loc[:, TS_COLS])
    else:
        scaler = StandardScaler()
        df.loc[ids_train, TS_COLS] = scaler.fit_transform(df.loc[ids_train, TS_COLS])
        df.loc[ids_val, TS_COLS] = scaler.transform(df.loc[ids_val, TS_COLS])
        df.loc[ids_test, TS_COLS] = scaler.transform(df.loc[ids_test, TS_COLS])

    df_ts = df.copy()[TS_COLS]
    df_extra = df.copy()[EXTRA_COLS]
    
    y_train = y_iicu.loc[ids_train]['y'].values
    y_val = y_iicu.loc[ids_val]['y'].values
    y_test = y_iicu.loc[ids_test]['y'].values
    
    data_dict_ts = dict(df_ts.groupby(df_ts.index).apply(lambda g: g.values))
    X_train_ts = [data_dict_ts[id_] for id_ in ids_train]
    X_val_ts = [data_dict_ts[id_] for id_ in ids_val]
    X_test_ts = [data_dict_ts[id_] for id_ in ids_test]
    
    data_dict_extra = dict(df_extra.groupby(df_extra.index).apply(lambda g: g.values))
    X_train_extra = [data_dict_extra[id_] for id_ in ids_train]
    X_val_extra = [data_dict_extra[id_] for id_ in ids_val]
    X_test_extra = [data_dict_extra[id_] for id_ in ids_test]
    
    if extra:
        train_data = Dataset(X_ts=X_train_ts, y=y_train, X_extra=X_train_extra)
        val_data = Dataset(X_ts=X_val_ts, y=y_val, X_extra=X_val_extra)
        test_data = Dataset(X_ts=X_test_ts, y=y_test, X_extra=X_test_extra)
    
    else:  
        train_data = Dataset(X_ts=X_train_ts, y=y_train, X_extra=None)
        val_data = Dataset(X_ts=X_val_ts, y=y_val, X_extra=None)
        test_data = Dataset(X_ts=X_test_ts, y=y_test, X_extra=None)
        
    return train_data, val_data, test_data

In [185]:
ids_train = iicu_ids[:100]
ids_val = iicu_ids[100:113]
ids_test = iicu_ids[113:]

print(len(ids_train))
print(len(ids_val))
print(len(ids_test))

100
13
50


In [190]:
def run(extra, transfer, hidden_dim=64, dropout=0.5, activation=nn.ReLU, weight_decay=1e-2, batch_size=32,
        patience=5, verbose=True, n=1):
    aucs = []
    rkf = RepeatedKFold(n_splits=5, n_repeats=n)
    for train_idx, test_idx in rkf.split(iicu_ids, iicu_labels):
        ids_train, ids_test = iicu_ids[train_idx], iicu_ids[test_idx]
        n_val = int(np.ceil(len(ids_train) * 0.2))
        ids_val = ids_train[-n_val:]
        ids_train = ids_train[:-n_val]

        iicu_train_data, iicu_val_data, iicu_test_data = load_iicu_fold(ids_train, ids_val, ids_test, extra=extra,
                                                                        transfer=transfer)



        #         iicu_train_data, iicu_val_data, iicu_test_data = load_iicu_fold(ids_train, ids_val, ids_test,
        #                                                                         extra=extra,
        #                                                                         transfer=transfer)
        #         #print(len(iicu_train_data))

        iicu_model = Model(iicu_train_data, hidden_dim=hidden_dim, dropout=dropout, activation=activation).cuda()
        iicu_model, iicu_model_best_val_auc = train(model=iicu_model,
                                                    optimizer=torch.optim.Adam(iicu_model.parameters(),
                                                                               weight_decay=weight_decay),
                                                    criterion=Loss(iicu_train_data, weighted=True),
                                                    train_loader=iicu_train_data.loader(batch_size=batch_size, shuffle=True),
                                                    val_loader=iicu_val_data.loader(batch_size=128, shuffle=False),
                                                    #val_loader=iicu_test_data.loader(batch_size=128, shuffle=False),
                                                    patience=patience,
                                                    verbose=verbose)
        test_auc = get_auc(iicu_model, iicu_test_data.loader(batch_size=128, shuffle=False))

        if verbose:
            print('Best val AUC = %.3f' % iicu_model_best_val_auc)
            print('Test AUC = %.3f' % test_auc)

        aucs.append(test_auc)
    
    print(confidence_interval(aucs))
    return aucs

In [198]:
a = run(n=100, verbose=False, extra=False, transfer=False, hidden_dim=32, batch_size=32, patience=10, activation=nn.Tanh,
    dropout=0.25, weight_decay=1e-2)

95% CI: 0.364-0.722


In [199]:
b = run(n=100, verbose=False, extra=True, transfer=False, hidden_dim=32, batch_size=32, patience=10, activation=nn.Tanh,
    dropout=0.25, weight_decay=1e-2)

95% CI: 0.383-0.712


In [200]:
c = run(n=100, verbose=False, extra=False, transfer=True, hidden_dim=32, batch_size=32, patience=10, activation=nn.Tanh,
    dropout=0.25, weight_decay=1e-2)

95% CI: 0.407-0.756


In [201]:
d = run(n=100, verbose=False, extra=True, transfer=True, hidden_dim=32, batch_size=32, patience=10, activation=nn.Tanh,
    dropout=0.25, weight_decay=1e-2)

95% CI: 0.343-0.680


In [24]:
aucs_no_extra_no_transfer = run_iicu(extra=False, transfer=False, n=100)

Mean AUROC after 100 runs = 0.589


In [33]:
confidence_interval(aucs_no_extra_transfer)

'95% CI: 0.628-0.836'

In [25]:
aucs_extra_no_transfer = run_iicu(extra=True, transfer=False, n=100)

Mean AUROC after 100 runs = 0.578


In [34]:
confidence_interval(aucs_extra_no_transfer)

'95% CI: 0.508-0.630'

In [26]:
aucs_no_extra_transfer = run_iicu(extra=False, transfer=True, n=100)

Mean AUROC after 100 runs = 0.765


In [35]:
confidence_interval(aucs_no_extra_transfer)

'95% CI: 0.628-0.836'

In [27]:
aucs_extra_transfer = run_iicu(extra=True, transfer=True, n=100)

Mean AUROC after 100 runs = 0.778


In [36]:
confidence_interval(aucs_extra_transfer)

'95% CI: 0.667-0.835'

In [37]:
163*.8

130.4

In [38]:
163*.2

32.6

In [39]:
130*.2

26.0

### Trying repeated KFold

In [ ]:
extra = False
transfer = False
n_repeats = 10

aucs = []

rkf = RepeatedKFold(n_splits=5, n_repeats=n_repeats)
for train_idx, test_idx in rkf.split(iicu_ids, iicu_labels):
    ids_train, ids_test = iicu_ids[train_idx], iicu_ids[test_idx]
    n_val = int(np.ceil(len(ids_train) * 0.2))
    ids_val = ids_train[-n_val:]
    ids_train = ids_train[:-n_val]

    iicu_train_data, iicu_val_data, iicu_test_data = load_iicu_fold(ids_train, ids_val, ids_test, extra=extra,
                                                                    transfer=transfer)

    iicu_model = Model(iicu_train_data).cuda()

    if transfer:
        iicu_model = transfer_weights(source_model=idealist_model, dest_model=iicu_model)

    iicu_model, iicu_model_best_val_auc = train(model=iicu_model,
                                              optimizer=torch.optim.Adam(iicu_model.parameters(), weight_decay=1e-2),
                                              criterion=Loss(iicu_train_data),
                                              train_loader=iicu_train_data.loader(batch_size=32, shuffle=True),
                                              val_loader=iicu_val_data.loader(batch_size=128, shuffle=False),
                                              patience=3,
                                              verbose=False)

    aucs.append(get_auc(iicu_model, iicu_test_data.loader(batch_size=128, shuffle=False)))
    
print(np.mean(aucs))

In [ ]:
np.mean(aucs)

In [ ]:
iicu_train_data.input_dim_ts

In [ ]:
iicu_train_data.input_dim_extra